<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Домашнее-задание-по-теме-&quot;Коническая-оптимизация-для-управления-портфелем&quot;" data-toc-modified-id="Домашнее-задание-по-теме-&quot;Коническая-оптимизация-для-управления-портфелем&quot;-1">Домашнее задание по теме "Коническая оптимизация для управления портфелем"</a></span></li><li><span><a href="#Задача-4" data-toc-modified-id="Задача-4-2">Задача 4</a></span></li><li><span><a href="#Задача-5" data-toc-modified-id="Задача-5-3">Задача 5</a></span></li><li><span><a href="#Задача-6" data-toc-modified-id="Задача-6-4">Задача 6</a></span></li><li><span><a href="#Задача-7-(сложная)" data-toc-modified-id="Задача-7-(сложная)-5">Задача 7 (сложная)</a></span></li></ul></div>

In [1]:
from math import sqrt
import numpy as np
from cvxopt import matrix
from cvxopt.blas import nrm2, dot
from cvxopt.solvers import qp, socp, options
import matplotlib.pyplot as plt
%matplotlib inline

# Домашнее задание по теме "Коническая оптимизация для управления портфелем"
для получение полного бала необходимо решить задачу 4 и одну из задач 5 или 6.

Задача 7 - задача для сомостоятельной работы для тех кто хочет больше углубиться в тему. Любые мысли на тему ее решения приветствуются, но в зачет по домашнему заданию не входят.

# Задача 4
Напишите функцию, которая решает задачу выбора оптимального портфеля Марковица по следующим входным данным: 

- матрица $A$ разложения инструментов по факторам: один размер $N$ определяет число инструментов, второй размер $K$ определяет число факторов;
- матрица $B$ ковариации факторов (порядок факторов считать согласованным с матрицей $A$;
- вектор $D$ длины $N$ идиосинкратического риска: компонента $i$ вектора равна $Var(\delta_i)$;
- вектор $\alpha$ ожидаемых доходностей инструментов;
- параметр "неприятия риска" $\lambda$;
- максимальная сумма всех позиций портфеля по абсолютной величине (maxGross); 
- флаг, разрешающий или запрещающий короткие (отрицательные) позиции инструментов в портфеле;
- в случае если короткие позиции разрешены, минимальная/максимальная сумма всех позиций портфеля (minNet / maxNet);

Требования к выходным данным: 

- позиции всех инструментов в портфеле; 
- позиции портфеля по всем факторам;
- риск портфеля и ожидаемую доходность.

Было бы очень хорошо аккуратно обрабатывать случаи, когда оптимизатор говорит, что проблема либо не имеет решения, либо выдет статус решения, отличный от Optimal solution found. 

Сигнатура функции:

In [29]:
def problem4(A, B, D, alpha, riskAversion, maxGross, allowShort=False, maxNet=None, minNet=None):
    # TODO : your code here
    pi = np.array([]) 
    pi_factors = np.array([]) 
    profit = 0.
    risk = 0.
    return pi, pi_factors, risk, profit

Когда решение готово запусите код в следующей ячейке, он распечатает результаты для некоторых вариантов расчета с тестовыми данными.

In [0]:
from test_data import factor_cov, stocks_to_factors, stock_specific_risk, stock_alpha, run_problem4_tests

A = stocks_to_factors.to_numpy().T
B = factor_cov.to_numpy()
D = np.diag( np.ravel( stock_specific_risk ) )
alpha = np.ravel( stock_alpha )

run_problem4_tests(solution=problem4, A=A, B=B, D=D, alpha=alpha)

# Задача 5
Добавьте в задачу оптимизации 4 линейные органичения по факторам. К входным данным добавляется список индексов факторов, для которых будут ограничения. Каждое ограничение представляет собой пару чисел: максимальное и минимальное значение суммарной позиции портфеля по фактору. 

# Задача 6
Модифицируйте функцию из задачи 3 или задачи 4 для решения задачи ребалансировки портфеля (см. слайд "Оптимальная ребалансировка портфеля" лекции). Имеется начальный портфель $w$, который требуется оптимально изменить путем добавления "вектора ребалансировки" $x$. Компоненты этого вектора могут быть как положительны (докупаем акций), так и отрицательными (продаем акции), но результирующий портфель $w+x$ должен иметь все положительные компоненты, причем 

$\sum_{i=1}^{N} w_i = \sum_{i=1} (w_i + x_i)$.

В модифицированной функции оптимизации Марковица добавляется сумма транзакционных издержек $TC(x)$. Издержки торговли одним инструментом не влияют на другие инструменты, они пропорциональны количеству проторгованного:

$TC(x) = \sum_{i=1}^{N} p_i |x_i|$.

Коэффициенты пропорциональности считаем постоянными величинами, зависящими отсвойств акции. Вектор этих коэффициентов добавляется в спсиок входных данных.

# Задача 7 (сложная)
Написать функцию, реализующую оптимальную ликвидацию портфеля  в несколько шагов. Имеется начальный портфель $w$, от которого нужно полностью избавиться за несколько шагов, то есть построить кусочно-линейную траекторию $w(t)$ с узлами $w_0= w$, $w_1, \ldots w_{k-1}, w_k = 0$. Число шагов $k$ известно заранее, это параметр задачи. Траектория ликвидации портфеля $w(t)$ должна быть монотонной по каждому инструменту. Траектория должна быть оптимальной в том смысле, что она минимизирует функционал 

$\lambda \int_{0}^{k} Var(w(t))\,dt + \sum_{j=1}^{k} TC(w_j - w{j-1})$

Транзакционные издержки в этом случае (в отличие от задачи 6) являются квадратичной функцией по каждому инструменту. 

Литературы по этой задаче в последние годы очень много, ищите по кодовымсловам Almgren - Chriss portfolio execution model.